In [1]:
import csv
import os

import tqdm

import biosppy.signals.ecg as ecg
import biosppy
import neurokit2 as nk

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import scipy as sp

import hrvanalysis
import heartpy as hp

import sys

sys.path.append("..")
from util import load_base_data


SAMPLING_RATE = 300.0
DATAPATH = "/Users/ericschreiber/dev/ETH/AML/Project_1/aml-2023/task2/data"

In [2]:
X_train, y_train, X_test = load_base_data()

In [3]:
def compute_hrv_features(peaks):
    try:
        tdf = hrvanalysis.get_time_domain_features(peaks)
        gf = hrvanalysis.get_geometrical_features(peaks)
        fdf = hrvanalysis.get_frequency_domain_features(peaks)
        pcp = hrvanalysis.get_poincare_plot_features(peaks)
        samp = hrvanalysis.get_sampen(peaks)
    except:
        return [0] * 22

    return [
        tdf["mean_nni"],
        tdf["sdnn"],
        tdf["sdsd"],
        tdf["nni_50"],
        tdf["pnni_50"],
        tdf["nni_20"],
        tdf["pnni_20"],
        tdf["rmssd"],
        tdf["median_nni"],
        tdf["range_nni"],
        tdf["cvsd"],
        tdf["cvnni"],
        tdf["mean_hr"],
        tdf["max_hr"],
        tdf["min_hr"],
        fdf["lf"],
        fdf["hf"],
        fdf["lf_hf_ratio"],
        pcp["sd1"],
        pcp["sd2"],
        pcp["ratio_sd2_sd1"],
        samp["sampen"],
    ]

In [4]:
def compute_hp_features(ecg):
    try:
        _, measures = hp.process(ecg, SAMPLING_RATE)
    except:
        try:
            _, measures = hp.process(hp.flip_signal(ecg), SAMPLING_RATE)
        except:
            return [0] * 12

    return [
        measures["bpm"],
        measures["ibi"],
        measures["sdnn"],
        measures["sdsd"],
        measures["rmssd"],
        measures["pnn20"],
        measures["pnn50"],
        measures["hr_mad"],
        measures["sd1"],
        measures["sd2"],
        measures["s"],
        np.log10(measures["sd1/sd2"] ** 2),
    ]

In [5]:
def clean_input(ecg):
    #  filtered using a finite impulse response bandpass filter
    cleaned = nk.ecg_clean(ecg, sampling_rate=SAMPLING_RATE, method="biosppy")
    cleaned, was_inverted = nk.ecg_invert(cleaned, sampling_rate=300, show=False)
    _, info = nk.ecg_peaks(ecg_cleaned=cleaned, sampling_rate=SAMPLING_RATE)
    rpeaks = info["ECG_R_Peaks"]
    return cleaned, rpeaks

In [6]:
def make_features(ecg):
    cleaned, rpeaks = clean_input(ecg)
    features = []
    features += compute_hp_features(cleaned)
    features += compute_hrv_features(rpeaks)
    features = np.array(features).flatten()
    return features


def make_features_from_df(df):
    features = []
    for i in tqdm.tqdm(range(len(df))):
        ecg = df.iloc[i].values
        features.append(make_features(ecg))
    numpy = np.array(features)
    df = pd.DataFrame(numpy).reset_index(drop=False)
    df.drop(columns=["index"], inplace=True)
    df.index.name = "id"

    return df

In [8]:
features_X_train = make_features_from_df(X_train)

  0%|          | 0/5117 [00:00<?, ?it/s]/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 1485 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
  0%|          | 1/5117 [00:00<38:25,  2.22it/s]/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 9254 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:153: FutureWarning: DataFrame.pad/Series.pad is deprecated. Use DataFrame.ffill/Series.ffill instead
  ecg_signal = pd.DataFrame.pad(pd.Series(ecg_signal))
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/scipy/interpolate/_fitpack2.py:280: UserWarning: 
A theoretically impossible result was found during the iteration
pr

In [9]:
features_X_train

0           1           2           3           4         5   \
id                                                                           
0     147.929374  405.598958  137.243406   34.685420  263.315979  1.000000   
1     270.962630  221.432749  153.799805  129.419914  225.587465  0.917431   
2     406.658740  147.543860  165.698388  117.934294  237.166709  1.000000   
3     148.094374  405.147059   78.331109   78.038511  104.253144  0.676923   
4      97.983422  612.348485   51.037615   12.623526   17.268214  0.186047   
...          ...         ...         ...         ...         ...       ...   
5112  344.899016  173.963964  114.182925  102.483775  158.985309  0.884058   
5113  370.599956  161.899642  124.066308  116.126814  207.596359  0.948052   
5114  246.442953  243.464052  148.660630  124.371273  240.027203  0.927835   
5115  216.867470  276.666667  184.453845  128.382814  295.007921  0.976471   
5116  101.478326  591.259259   35.564505    8.796691   14.915587  0.159091   

            6           7           8           9   ...         24  \
id                                                  ...              
0     1.000000  131.666667  186.183195   53.144026  ...  27.403847   
1     0.770642  153.333333  159.474032  149.948851  ...  32.412754   
2     0.945946   70.000000  167.642892  167.257172  ...  33.532124   
3     0.369231   23.333333   73.702371   82.349378  ...  33.421030   
4     0.023256   15.000000   12.209979   71.861050  ...  32.958559   
...        ...         ...         ...         ...  ...        ...   
5112  0.666667   85.000000  112.398330  120.067690  ...  36.420775   
5113  0.870130   83.333333  146.628240  105.239084  ...  44.384811   
5114  0.865979  116.666667  169.514080  122.075249  ...  40.933608   
5115  0.929412  170.000000  208.484095  153.508891  ...  42.684035   
5116  0.000000   20.000000   10.546777   49.750843  ...  29.970592   

              25         26          27        28          29         30  \
id                                                                         
0     594.059406   3.690945  200.235003  0.223621  895.421767  13.786725   
1     327.868852   7.076306  620.932932  1.962904  316.333846  14.402293   
2     309.278351   7.471980  906.090860  1.175528  770.794483   7.597883   
3     508.474576   6.954103  274.532781  1.373484  199.880645  15.548627   
4     357.142857   7.116594  312.336083  0.403520  774.028480  10.833753   
...          ...        ...         ...       ...         ...        ...   
5112  199.335548  11.820331  786.574809  6.872229  114.457012  44.199825   
5113  606.060606   7.367387  586.347251  1.551529  377.915750  11.091845   
5114  508.474576   7.127584  701.632331  0.846470  828.892312  20.044174   
5115  582.524272   7.275373  629.130067  0.916589  686.382055   5.932415   
5116  253.164557   7.461758  357.785232  0.428579  834.816688   7.717529   

               31          32        33  
id                                       
0     6761.714180  490.451094  0.005089  
1     3512.042128  243.852980  0.099091  
2     3366.705881  443.111021 -0.000000  
3     3528.866446  226.956787  0.021693  
4     3541.244920  326.871487 -0.000000  
...           ...         ...       ...  
5112  2126.774028   48.117250  0.044452  
5113  3429.076703  309.152951 -0.000000  
5114  3576.350191  178.423427  0.038466  
5115  3473.121484  585.448161 -0.000000  
5116  3282.556562  425.337769 -0.000000  

[5117 rows x 34 columns]

In [10]:
# How many infs
print(f"Number of infs: {np.sum(np.isinf(features_X_train), axis=0).sum()}")
# Which columns have infs
cols_with_infs = np.where(np.isinf(features_X_train))[1]
cols_with_infs_unique = np.unique(cols_with_infs)
print(f"Columns with infs: {len(cols_with_infs_unique)}")
print(
    f"biggest pos value except inf: {np.max(features_X_train[features_X_train != np.inf].max())}"
)
print(f"biggest neg value: {np.min(features_X_train).min()}")
biggest_pos = np.max(features_X_train[features_X_train != np.inf].max())
biggest_neg = np.min(features_X_train).min()
# Replace infs with biggest pos value
features_X_train[features_X_train == np.inf] = biggest_pos
# Replace -infs with biggest neg value
features_X_train[features_X_train == -np.inf] = biggest_neg

Number of infs: 222
Columns with infs: 1
biggest pos value except inf: 283374.275266772
biggest neg value: -2.958154171416197


In [11]:
X_train_save_path = os.path.join(DATAPATH, "feature_extraction/hrv_X_train.csv")
features_X_train.to_csv(X_train_save_path, index=True)

# X Test

In [13]:
test_features = make_features_from_df(X_test)

# How many infs
print(f"Number of infs: {np.sum(np.isinf(test_features), axis=0).sum()}")
# Which columns have infs
cols_with_infs = np.where(np.isinf(test_features))[1]
cols_with_infs_unique = np.unique(cols_with_infs)
print(f"Columns with infs: {len(cols_with_infs_unique)}")
print(
    f"biggest pos value except inf: {np.max(test_features[test_features != np.inf].max())}"
)
print(
    f"biggest neg value excpet inf : {np.min(test_features[test_features != -np.inf]).min()}"
)
biggest_pos = np.max(test_features[test_features != np.inf].max())
biggest_neg = np.min(test_features[test_features != -np.inf]).min()
# Replace infs with biggest pos value
test_features[test_features == np.inf] = biggest_pos
# Replace -infs with biggest neg value
test_features[test_features == -np.inf] = biggest_neg

  0%|          | 0/3411 [00:00<?, ?it/s]/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 9658 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:153: FutureWarning: DataFrame.pad/Series.pad is deprecated. Use DataFrame.ffill/Series.ffill instead
  ecg_signal = pd.DataFrame.pad(pd.Series(ecg_signal))
  0%|          | 1/3411 [00:00<06:03,  9.39it/s]/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:101: NeuroKitWarning: There are 11998 missing data points in your signal. Filling missing values by using the forward filling method.
  warn(
/Users/ericschreiber/miniconda3/envs/ml/lib/python3.10/site-packages/neurokit2/ecg/ecg_clean.py:153: FutureWarning: DataFrame.pad/Series.pad is deprecated. Use DataFrame.ffill/Series.ff

Number of infs: 117
Columns with infs: 1
biggest pos value except inf: 260290.5498992953
biggest neg value excpet inf : -2.770324381472468


In [14]:
X_test_save_path = os.path.join(DATAPATH, "feature_extraction/hrv_X_test.csv")
test_features.to_csv(X_test_save_path, index=True)